# Extracció d'entitats anomenades (Pràctica 3)

In [1]:
import nltk
nltk.download('conll2002')
from nltk.corpus import conll2002
from nltk.tag import CRFTagger

[nltk_data] Downloading package conll2002 to
[nltk_data]     C:\Users\Usuario\AppData\Roaming\nltk_data...
[nltk_data]   Package conll2002 is already up-to-date!


Aquests corpus contindran llistes d'oracions, on cada oració està representada com una llista de tuples, que representen paraules i etiquetes, seguint el format BIO (Inside-Outside-Beginning), comunament utilitzat en tasques de reconeixement d'entitats anomenades.

Dev: porción del conjunto de datos que se reserva con el propósito de ajustar los hiperparámetros del modelo, seleccionar características óptimas y evaluar el rendimiento del modelo en datos no vistos durante el entrenamiento

In [20]:
train_esp = conll2002.iob_sents('esp.train')
dev_esp = conll2002.iob_sents('esp.testa')
test_esp = conll2002.iob_sents('esp.testb')

In [21]:
train_ned = conll2002.iob_sents('ned.train')
dev_ned = conll2002.iob_sents('ned.testa')
test_ned = conll2002.iob_sents('ned.testb')

per fer despres lo de train de crftagger necessita tuples de (paraula, tag) i ara mateix tenim (paraula, tag,iob), per tant eliminem la columna iob

In [22]:
# Eliminar la tercera columna (IOB) de los datos de entrenamiento
train_esp = [[(word, tag) for word, tag, _ in sent] for sent in train_esp]

train_ned = [[(word, tag) for word, tag, _ in sent] for sent in train_ned]

In [23]:
train_esp #Ho he posat per comparar que estigui ben fet

[[('Melbourne', 'NP'),
  ('(', 'Fpa'),
  ('Australia', 'NP'),
  (')', 'Fpt'),
  (',', 'Fc'),
  ('25', 'Z'),
  ('may', 'NC'),
  ('(', 'Fpa'),
  ('EFE', 'NC'),
  (')', 'Fpt'),
  ('.', 'Fp')],
 [('-', 'Fg')],
 [('El', 'DA'),
  ('Abogado', 'NC'),
  ('General', 'AQ'),
  ('del', 'SP'),
  ('Estado', 'NC'),
  (',', 'Fc'),
  ('Daryl', 'VMI'),
  ('Williams', 'NC'),
  (',', 'Fc'),
  ('subrayó', 'VMI'),
  ('hoy', 'RG'),
  ('la', 'DA'),
  ('necesidad', 'NC'),
  ('de', 'SP'),
  ('tomar', 'VMN'),
  ('medidas', 'NC'),
  ('para', 'SP'),
  ('proteger', 'VMN'),
  ('al', 'SP'),
  ('sistema', 'NC'),
  ('judicial', 'AQ'),
  ('australiano', 'AQ'),
  ('frente', 'RG'),
  ('a', 'SP'),
  ('una', 'DI'),
  ('página', 'NC'),
  ('de', 'SP'),
  ('internet', 'NC'),
  ('que', 'PR'),
  ('imposibilita', 'VMI'),
  ('el', 'DA'),
  ('cumplimiento', 'NC'),
  ('de', 'SP'),
  ('los', 'DA'),
  ('principios', 'NC'),
  ('básicos', 'AQ'),
  ('de', 'SP'),
  ('la', 'DA'),
  ('Ley', 'NC'),
  ('.', 'Fp')],
 [('La', 'DA'),
  ('petición

entrenem el model per español

In [25]:
#tarda bastant en executar-se

# Crear una instancia de CRFTagger
crf_tagger_esp = CRFTagger()

# Entrenar el modelo CRF con los datos de entrenamiento en español
crf_tagger_esp.train(train_esp, 'model_crf_esp.crf.tagger')

entrenem el model per neerlandes

In [ ]:
# Crear una nueva instancia de CRFTagger para neerlandés
crf_tagger_ned = CRFTagger()

# Entrenar el modelo CRF con los datos de entrenamiento en neerlandés
crf_tagger_ned.train(train_ned, 'model_crf_ned.crf.tagger')

validació pel model en expañol

In [ ]:
#Ara etiquetas té la paraula i el tag predit: '[[('Sao', 'NC'),('Paulo', 'VMI'),('(', 'Fpa'),'

etiquetadas_dev_esp = crf_tagger_esp.tag_sents([word for word, _, _ in sent] for sent in dev_esp)

etiquetadas_dev_esp


In [ ]:
#dev_esp originalment es (paraula,tag, bio), com estem predint la tag, eliminem el bio per validar el model
dev_esp = [[(word, tag) for word, tag, _ in sent] for sent in dev_esp]

# Calcular la precisión
def calcular_precision(etiquetadas_pred, etiquetadas_reales):
    total = sum(len(etiquetadas_reales[i]) for i in range(len(etiquetadas_reales)))
    correctas = sum(1 for sent_pred, sent_real in zip(etiquetadas_pred, etiquetadas_reales)
                    for (_, pred), (_, real) in zip(sent_pred, sent_real) if pred == real)
    return correctas / total

# Obtener las etiquetas reales
etiquetas_reales_dev_esp = dev_esp

# Calcular la precisión
precision = calcular_precision(etiquetadas_dev_esp, etiquetas_reales_dev_esp)

print("Precisión del modelo:", precision)


validació pel model en neerlandes

In [ ]:
etiquetadas_dev_ned = crf_tagger_ned.tag_sents([word for word, _, _ in sent] for sent in dev_ned)

etiquetadas_dev_ned

In [ ]:
dev_ned = [[(word, tag) for word, tag, _ in sent] for sent in dev_ned]
#provaa
# Obtener las etiquetas reales
etiquetas_reales_dev_ned = dev_ned

# Calcular la precisión
precision = calcular_precision(etiquetadas_dev_ned, etiquetas_reales_dev_ned)

print("Precisión del modelo:", precision)

# Experiments amb diferents codificacions BIO, IO, BIOS

### Funcions per avaluar els models

In [2]:
def extract_real_entities(sentences):
    entities = []
    for sentence in sentences:
        entity = []
        for word, tag in sentence:
            if tag != 'O':
                if entity and tag[0] != 'I':
                    entities.append(tuple(entity))
                    entity = [(word, tag[0:])]
                elif entity:
                    entity.append((word, tag[0:]))
                else:
                    entity = [(word, tag[0:])]
            elif entity:
                entities.append(tuple(entity))
                entity = []
        if entity:
            entities.append(tuple(entity))
    return entities

In [3]:
def calculate_metrics(predicted_entities, real_entities):
    true_positives = len(predicted_entities.intersection(real_entities))
    if len(predicted_entities) == 0:
        precision = 0
    else:
        precision = true_positives / len(predicted_entities)
    if len(real_entities) == 0:
        recall = 0
    else:
        recall = true_positives / len(real_entities)
    if precision + recall == 0:
        f1_score = 0
    else:
        f1_score = 2 * (precision * recall) / (precision + recall)
    return precision, recall, f1_score


## Experiments amb BIO

En espanyol

In [4]:
train_esp = conll2002.iob_sents('esp.train')
dev_esp = conll2002.iob_sents('esp.testa')
test_esp = conll2002.iob_sents('esp.testb')

In [5]:
train_esp = [[(word, BIO) for word, _, BIO in sent] for sent in train_esp]
dev_esp = [[(word, BIO) for word, _, BIO in sent] for sent in dev_esp]

train_esp #per comprovar que esta ben fet

[[('Melbourne', 'B-LOC'),
  ('(', 'O'),
  ('Australia', 'B-LOC'),
  (')', 'O'),
  (',', 'O'),
  ('25', 'O'),
  ('may', 'O'),
  ('(', 'O'),
  ('EFE', 'B-ORG'),
  (')', 'O'),
  ('.', 'O')],
 [('-', 'O')],
 [('El', 'O'),
  ('Abogado', 'B-PER'),
  ('General', 'I-PER'),
  ('del', 'I-PER'),
  ('Estado', 'I-PER'),
  (',', 'O'),
  ('Daryl', 'B-PER'),
  ('Williams', 'I-PER'),
  (',', 'O'),
  ('subrayó', 'O'),
  ('hoy', 'O'),
  ('la', 'O'),
  ('necesidad', 'O'),
  ('de', 'O'),
  ('tomar', 'O'),
  ('medidas', 'O'),
  ('para', 'O'),
  ('proteger', 'O'),
  ('al', 'O'),
  ('sistema', 'O'),
  ('judicial', 'O'),
  ('australiano', 'O'),
  ('frente', 'O'),
  ('a', 'O'),
  ('una', 'O'),
  ('página', 'O'),
  ('de', 'O'),
  ('internet', 'O'),
  ('que', 'O'),
  ('imposibilita', 'O'),
  ('el', 'O'),
  ('cumplimiento', 'O'),
  ('de', 'O'),
  ('los', 'O'),
  ('principios', 'O'),
  ('básicos', 'O'),
  ('de', 'O'),
  ('la', 'O'),
  ('Ley', 'B-MISC'),
  ('.', 'O')],
 [('La', 'O'),
  ('petición', 'O'),
  ('del', '

In [6]:
# Crear una instancia de CRFTagger
crf_tagger_esp = CRFTagger()

# Entrenar el modelo CRF con los datos de entrenamiento en español
crf_tagger_esp.train(train_esp, 'model_crf_esp.crf.tagger')

In [7]:
etiquetadas_dev_esp = crf_tagger_esp.tag_sents([word for word, _ in sent] for sent in dev_esp)
etiquetadas_dev_esp

[[('Sao', 'B-LOC'),
  ('Paulo', 'I-LOC'),
  ('(', 'O'),
  ('Brasil', 'B-LOC'),
  (')', 'O'),
  (',', 'O'),
  ('23', 'O'),
  ('may', 'O'),
  ('(', 'O'),
  ('EFECOM', 'B-ORG'),
  (')', 'O'),
  ('.', 'O')],
 [('-', 'O')],
 [('La', 'O'),
  ('multinacional', 'O'),
  ('española', 'O'),
  ('Telefónica', 'B-ORG'),
  ('ha', 'O'),
  ('impuesto', 'O'),
  ('un', 'O'),
  ('récord', 'O'),
  ('mundial', 'O'),
  ('al', 'O'),
  ('poner', 'O'),
  ('en', 'O'),
  ('servicio', 'O'),
  ('tres', 'O'),
  ('millones', 'O'),
  ('de', 'O'),
  ('nuevas', 'O'),
  ('líneas', 'O'),
  ('en', 'O'),
  ('el', 'O'),
  ('estado', 'O'),
  ('brasileño', 'O'),
  ('de', 'O'),
  ('Sao', 'B-LOC'),
  ('Paulo', 'I-LOC'),
  ('desde', 'O'),
  ('que', 'O'),
  ('asumió', 'O'),
  ('el', 'O'),
  ('control', 'O'),
  ('de', 'O'),
  ('la', 'O'),
  ('operadora', 'O'),
  ('Telesp', 'B-ORG'),
  ('hace', 'O'),
  ('20', 'O'),
  ('meses', 'O'),
  (',', 'O'),
  ('anunció', 'O'),
  ('hoy', 'O'),
  ('el', 'O'),
  ('presidente', 'O'),
  ('de', 'O')

In [8]:
real_entities = extract_real_entities(dev_esp)
predicted_entities = extract_real_entities(etiquetadas_dev_esp)

In [9]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.6553374820488271
Recall: 0.6202990484821024
F1-score: 0.6373370577281192


En neerlandes

In [10]:
train_ned = conll2002.iob_sents('ned.train')
dev_ned = conll2002.iob_sents('ned.testa')
test_ned = conll2002.iob_sents('ned.testb')

In [11]:
train_ned = [[(word, BIO) for word, _, BIO in sent] for sent in train_ned]
dev_ned = [[(word, BIO) for word, _, BIO in sent] for sent in dev_ned]

In [12]:
# Crear una nueva instancia de CRFTagger para neerlandés
crf_tagger_ned = CRFTagger()

# Entrenar el modelo CRF con los datos de entrenamiento en neerlandés
crf_tagger_ned.train(train_ned, 'model_crf_ned.crf.tagger')

In [13]:
etiquetadas_dev_ned = crf_tagger_ned.tag_sents([word for word, _ in sent] for sent in dev_ned)
etiquetadas_dev_ned

[[('Dat', 'O'),
  ('is', 'O'),
  ('verder', 'O'),
  ('opgelaaid', 'O'),
  ('door', 'O'),
  ('windsnelheden', 'O'),
  ('die', 'O'),
  ('oplopen', 'O'),
  ('tot', 'O'),
  ('35', 'O'),
  ('kilometer', 'O'),
  ('per', 'O'),
  ('uur', 'O'),
  ('.', 'O')],
 [('Bomaanslag', 'O'),
  ('op', 'O'),
  ('Indiase', 'B-MISC'),
  ('trein', 'O'),
  (':', 'O'),
  ('twaalf', 'O'),
  ('doden', 'O')],
 [('Ook', 'O'),
  ('in', 'O'),
  ('Californië', 'B-LOC'),
  (',', 'O'),
  ('in', 'O'),
  ('Sierra', 'B-LOC'),
  ('Nevada', 'I-LOC'),
  (',', 'O'),
  ('woeden', 'O'),
  ('al', 'O'),
  ('een', 'O'),
  ('week', 'O'),
  ('lang', 'O'),
  ('hevige', 'O'),
  ('bosbranden', 'O'),
  ('.', 'O')],
 [('De', 'O'),
  ('brand', 'O'),
  ('heeft', 'O'),
  ('vooral', 'O'),
  ('het', 'O'),
  ('nationale', 'O'),
  ('park', 'O'),
  ('van', 'O'),
  ('de', 'O'),
  ('Sequoia-indianen', 'B-MISC'),
  ('getroffen', 'O'),
  ('.', 'O')],
 [('De', 'O'),
  ('gestrande', 'O'),
  ('Concorde', 'O'),
  ('wordt', 'O'),
  ('nu', 'O'),
  ('aan', 

In [14]:
real_entities = extract_real_entities(dev_ned)
predicted_entities = extract_real_entities(etiquetadas_dev_ned)

In [15]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.5754795663052544
Recall: 0.5424528301886793
F1-score: 0.5584783488466207


## Experiment amb IO

En espanyol

In [16]:
train_esp = conll2002.iob_sents('esp.train')
dev_esp = conll2002.iob_sents('esp.testa')
test_esp = conll2002.iob_sents('esp.testb')

In [17]:
#no agafem el tag
train_esp = [[(word, BIO) for word, _, BIO in sent] for sent in train_esp]
dev_esp = [[(word, BIO) for word, _, BIO in sent] for sent in dev_esp]
test_esp = [[(word, BIO) for word, _, BIO in sent] for sent in test_esp]

In [18]:
#aquest codi canvia les B per I per tenir codificaciío IO
train_esp = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in train_esp]
train_esp

[[('Melbourne', 'I-LOC'),
  ('(', 'O'),
  ('Australia', 'I-LOC'),
  (')', 'O'),
  (',', 'O'),
  ('25', 'O'),
  ('may', 'O'),
  ('(', 'O'),
  ('EFE', 'I-ORG'),
  (')', 'O'),
  ('.', 'O')],
 [('-', 'O')],
 [('El', 'O'),
  ('Abogado', 'I-PER'),
  ('General', 'I-PER'),
  ('del', 'I-PER'),
  ('Estado', 'I-PER'),
  (',', 'O'),
  ('Daryl', 'I-PER'),
  ('Williams', 'I-PER'),
  (',', 'O'),
  ('subrayó', 'O'),
  ('hoy', 'O'),
  ('la', 'O'),
  ('necesidad', 'O'),
  ('de', 'O'),
  ('tomar', 'O'),
  ('medidas', 'O'),
  ('para', 'O'),
  ('proteger', 'O'),
  ('al', 'O'),
  ('sistema', 'O'),
  ('judicial', 'O'),
  ('australiano', 'O'),
  ('frente', 'O'),
  ('a', 'O'),
  ('una', 'O'),
  ('página', 'O'),
  ('de', 'O'),
  ('internet', 'O'),
  ('que', 'O'),
  ('imposibilita', 'O'),
  ('el', 'O'),
  ('cumplimiento', 'O'),
  ('de', 'O'),
  ('los', 'O'),
  ('principios', 'O'),
  ('básicos', 'O'),
  ('de', 'O'),
  ('la', 'O'),
  ('Ley', 'I-MISC'),
  ('.', 'O')],
 [('La', 'O'),
  ('petición', 'O'),
  ('del', '

In [19]:
dev_esp = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in dev_esp]
test_esp = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in test_esp]

In [20]:
# Crear una instancia de CRFTagger
crf_tagger_esp = CRFTagger()

# Entrenar el modelo CRF con los datos de entrenamiento en español
crf_tagger_esp.train(train_esp, 'model_crf_esp.crf.tagger')

In [21]:
etiquetadas_dev_esp = crf_tagger_esp.tag_sents([word for word, _ in sent] for sent in dev_esp)

etiquetadas_dev_esp

[[('Sao', 'I-LOC'),
  ('Paulo', 'I-LOC'),
  ('(', 'O'),
  ('Brasil', 'I-LOC'),
  (')', 'O'),
  (',', 'O'),
  ('23', 'O'),
  ('may', 'O'),
  ('(', 'O'),
  ('EFECOM', 'I-ORG'),
  (')', 'O'),
  ('.', 'O')],
 [('-', 'O')],
 [('La', 'O'),
  ('multinacional', 'O'),
  ('española', 'O'),
  ('Telefónica', 'I-ORG'),
  ('ha', 'O'),
  ('impuesto', 'O'),
  ('un', 'O'),
  ('récord', 'O'),
  ('mundial', 'O'),
  ('al', 'O'),
  ('poner', 'O'),
  ('en', 'O'),
  ('servicio', 'O'),
  ('tres', 'O'),
  ('millones', 'O'),
  ('de', 'O'),
  ('nuevas', 'O'),
  ('líneas', 'O'),
  ('en', 'O'),
  ('el', 'O'),
  ('estado', 'O'),
  ('brasileño', 'O'),
  ('de', 'O'),
  ('Sao', 'I-LOC'),
  ('Paulo', 'I-LOC'),
  ('desde', 'O'),
  ('que', 'O'),
  ('asumió', 'O'),
  ('el', 'O'),
  ('control', 'O'),
  ('de', 'O'),
  ('la', 'O'),
  ('operadora', 'O'),
  ('Telesp', 'I-ORG'),
  ('hace', 'O'),
  ('20', 'O'),
  ('meses', 'O'),
  (',', 'O'),
  ('anunció', 'O'),
  ('hoy', 'O'),
  ('el', 'O'),
  ('presidente', 'O'),
  ('de', 'O')

In [22]:
real_entities = extract_real_entities(dev_esp)
predicted_entities = extract_real_entities(etiquetadas_dev_esp)

In [ ]:
real_entities

In [ ]:
predicted_entities

In [23]:

precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)


Precision: 0.6259765625
Recall: 0.5816696914700544
F1-score: 0.6030103480714959


En neerlandes

In [33]:
train_ned = conll2002.iob_sents('ned.train')
dev_ned = conll2002.iob_sents('ned.testa')
test_ned = conll2002.iob_sents('ned.testb')

In [25]:
train_ned = [[(word, BIO) for word, _, BIO in sent] for sent in train_ned]
dev_ned = [[(word, BIO) for word, _, BIO in sent] for sent in dev_ned]
test_ned = [[(word, BIO) for word, _, BIO in sent] for sent in test_ned]

In [27]:
train_ned = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in train_ned]
dev_ned = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in dev_ned]
test_ned = [[(word, 'I-' + bio[2:]) if bio.startswith('B-') else (word, bio) for word, bio in sent] for sent in test_ned]

In [28]:
# Crear una nueva instancia de CRFTagger para neerlandés
crf_tagger_ned = CRFTagger()

# Entrenar el modelo CRF con los datos de entrenamiento en neerlandés
crf_tagger_ned.train(train_ned, 'model_crf_ned.crf.tagger')

In [29]:
etiquetadas_dev_ned = crf_tagger_ned.tag_sents([word for word, _ in sent] for sent in dev_ned)
etiquetadas_dev_ned

[[('Dat', 'O'),
  ('is', 'O'),
  ('verder', 'O'),
  ('opgelaaid', 'O'),
  ('door', 'O'),
  ('windsnelheden', 'O'),
  ('die', 'O'),
  ('oplopen', 'O'),
  ('tot', 'O'),
  ('35', 'O'),
  ('kilometer', 'O'),
  ('per', 'O'),
  ('uur', 'O'),
  ('.', 'O')],
 [('Bomaanslag', 'O'),
  ('op', 'O'),
  ('Indiase', 'I-MISC'),
  ('trein', 'O'),
  (':', 'O'),
  ('twaalf', 'O'),
  ('doden', 'O')],
 [('Ook', 'O'),
  ('in', 'O'),
  ('Californië', 'I-LOC'),
  (',', 'O'),
  ('in', 'O'),
  ('Sierra', 'I-LOC'),
  ('Nevada', 'I-LOC'),
  (',', 'O'),
  ('woeden', 'O'),
  ('al', 'O'),
  ('een', 'O'),
  ('week', 'O'),
  ('lang', 'O'),
  ('hevige', 'O'),
  ('bosbranden', 'O'),
  ('.', 'O')],
 [('De', 'O'),
  ('brand', 'O'),
  ('heeft', 'O'),
  ('vooral', 'O'),
  ('het', 'O'),
  ('nationale', 'O'),
  ('park', 'O'),
  ('van', 'O'),
  ('de', 'O'),
  ('Sequoia-indianen', 'I-MISC'),
  ('getroffen', 'O'),
  ('.', 'O')],
 [('De', 'O'),
  ('gestrande', 'O'),
  ('Concorde', 'O'),
  ('wordt', 'O'),
  ('nu', 'O'),
  ('aan', 

In [30]:
real_entities = extract_real_entities(dev_ned)
predicted_entities = extract_real_entities(etiquetadas_dev_ned)

In [31]:
precision, recall, f1_score = calculate_metrics(set(predicted_entities), set(real_entities))
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)

Precision: 0.5575146935348446
Recall: 0.530775379696243
F1-score: 0.5438165438165439


## Experiment amb BIOW

In [ ]:
train_esp = conll2002.iob_sents('esp.train')
dev_esp = conll2002.iob_sents('esp.testa')
test_esp = conll2002.iob_sents('esp.testb')

In [ ]:
#no agafem el tag
train_esp = [[(word, BIO) for word, _, BIO in sent] for sent in train_esp]
dev_esp = [[(word, BIO) for word, _, BIO in sent] for sent in dev_esp]
test_esp = [[(word, BIO) for word, _, BIO in sent] for sent in test_esp]

In [ ]:
# Definir la función para convertir de BIO a BIOW
def bio_to_biow(sentences):
    biow_sentences = []
    current_entity = None
    for sent in sentences:
        biow_sent = []
        for i, (word, bio_tag) in enumerate(sent):
            if bio_tag == 'O':
                if current_entity:
                    biow_sent.append((word, current_entity + '-W'))
            else:
                prefix = bio_tag[0]
                entity_type = bio_tag[2:]
                if prefix == 'B':
                    if current_entity:
                        biow_sent.append((word, current_entity + '-W'))
                    current_entity = entity_type
                    biow_sent.append((word, 'B-' + entity_type))
                elif prefix == 'I':
                    if current_entity == entity_type:
                        biow_sent.append((word, 'I-' + entity_type))
                    else:
                        biow_sent.append((word, 'B-' + entity_type))
                        current_entity = entity_type
        biow_sentences.append(biow_sent)
    return biow_sentences



In [ ]:
train_esp = bio_to_biow(train_esp)
train_esp

QUAN FAS AQUETES QCOSES ENTRENAR AMB (PARAULA, BIO) NO AMB EL TAGGER

In [ ]:
from nltk.tag import CRFTagger
from nltk.corpus import wordnet

def custom_feature_func(tokens, idx):
    """
    Función de extracción de características personalizada.
    """
    word = tokens[idx]

    # Características básicas
    features = {
        'word': word,
        'is_upper': word.isupper(),
        'has_punctuation': any(char in '.,;:!?¡¿' for char in word),
        'has_digits': any(char.isdigit() for char in word),
        'suffix_2': word[-2:],
        'suffix_3': word[-3:],
        # Otras características adicionales
        'length': len(word),
        'prefix_2': word[:2],
        'prefix_3': word[:3],
        'lemma': wordnet.morphy(word) or word,  # lema de la palabra utilizando WordNet
        'pos_tag': nltk.pos_tag([word])[0][1],  # etiqueta de parte del discurso (POS tag)
        # Puedes agregar más características aquí según tus necesidades
    }

    return features

# Crear una instancia de CRFTagger con la función de características personalizada
crf_tagger_custom = CRFTagger(feature_func=custom_feature_func)

# Entrenar el modelo con los datos de entrenamiento
crf_tagger_custom.train(train_esp, 'model_crf_custom.crf.tagger')

# Evaluar el modelo en el conjunto de desarrollo
accuracy_custom = crf_tagger_custom.accuracy(dev_esp)
print("Precisión del modelo con características adicionales:", accuracy_custom)


## BIOES

In [ ]:
nltk.download('popular')

In [ ]:
from nltk.tag import CRFTagger

# Función para convertir etiquetas BIO a BIOES
def convert_bio_to_bioes(bio_tags):
    bioes_tags = []
    for i, (word, tag) in enumerate(bio_tags):
        if tag == 'O':
            bioes_tags.append((word, tag))
        elif tag.startswith('B-'):
            if i + 1 < len(bio_tags) and bio_tags[i + 1][1].startswith('I-'):
                bioes_tags.append((word, tag))
            else:
                bioes_tags.append((word, tag.replace('B-', 'S-')))
        elif tag.startswith('I-'):
            if i + 1 < len(bio_tags) and bio_tags[i + 1][1].startswith('I-'):
                bioes_tags.append((word, tag))
            else:
                bioes_tags.append((word, tag.replace('I-', 'E-')))
    return bioes_tags

# Convertir datos de entrenamiento y prueba a BIOES
train_esp_bioes = [convert_bio_to_bioes(sent) for sent in train_esp]
dev_esp_bioes = [convert_bio_to_bioes(sent) for sent in dev_esp]
test_esp_bioes = [convert_bio_to_bioes(sent) for sent in test_esp]

# Crear una instancia de CRFTagger
crf_tagger_esp = CRFTagger()

# Entrenar el modelo CRF con los datos de entrenamiento en español convertidos a BIOES
crf_tagger_esp.train(train_esp_bioes, 'model_crf_esp_bioes.crf.tagger')

# Etiquetar los conjuntos de desarrollo y prueba
etiquetadas_dev_esp_bioes = crf_tagger_esp.tag_sents([[word for word, _ in sent] for sent in dev_esp_bioes])
etiquetadas_test_esp_bioes = crf_tagger_esp.tag_sents([[word for word, _ in sent] for sent in test_esp_bioes])

# Comparar las etiquetas predichas con las reales para calcular la precisión
def calcular_precision(predichas, reales):
    correctos = sum(1 for pred_sent, real_sent in zip(predichas, reales) for pred, real in zip(pred_sent, real_sent) if pred[1] == real[1])
    total = sum(len(sent) for sent in reales)
    return correctos / total

precision_dev = calcular_precision(etiquetadas_dev_esp_bioes, dev_esp_bioes)
precision_test = calcular_precision(etiquetadas_test_esp_bioes, test_esp_bioes)

print("Precisión en conjunto de desarrollo:", precision_dev)
print("Precisión en conjunto de prueba:", precision_test)


## BIOES

In [ ]:
nltk.download('popular')

[nltk_data] Downloading collection 'popular'
[nltk_data]    | 
[nltk_data]    | Downloading package cmudict to C:\Users\Lola Monroy
[nltk_data]    |     Mir\AppData\Roaming\nltk_data...
[nltk_data]    |   Unzipping corpora\cmudict.zip.
[nltk_data]    | Downloading package gazetteers to C:\Users\Lola
[nltk_data]    |     Monroy Mir\AppData\Roaming\nltk_data...
[nltk_data]    |   Unzipping corpora\gazetteers.zip.
[nltk_data]    | Downloading package genesis to C:\Users\Lola Monroy
[nltk_data]    |     Mir\AppData\Roaming\nltk_data...
[nltk_data]    |   Unzipping corpora\genesis.zip.
[nltk_data]    | Downloading package gutenberg to C:\Users\Lola Monroy
[nltk_data]    |     Mir\AppData\Roaming\nltk_data...
[nltk_data]    |   Unzipping corpora\gutenberg.zip.
[nltk_data]    | Downloading package inaugural to C:\Users\Lola Monroy
[nltk_data]    |     Mir\AppData\Roaming\nltk_data...
[nltk_data]    |   Unzipping corpora\inaugural.zip.
[nltk_data]    | Downloading package movie_reviews to C:\U

True

In [ ]:
from nltk.tag import CRFTagger

# Función para convertir etiquetas BIO a BIOES
def convert_bio_to_bioes(bio_tags):
    bioes_tags = []
    for i, (word, tag) in enumerate(bio_tags):
        if tag == 'O':
            bioes_tags.append((word, tag))
        elif tag.startswith('B-'):
            if i + 1 < len(bio_tags) and bio_tags[i + 1][1].startswith('I-'):
                bioes_tags.append((word, tag))
            else:
                bioes_tags.append((word, tag.replace('B-', 'S-')))
        elif tag.startswith('I-'):
            if i + 1 < len(bio_tags) and bio_tags[i + 1][1].startswith('I-'):
                bioes_tags.append((word, tag))
            else:
                bioes_tags.append((word, tag.replace('I-', 'E-')))
    return bioes_tags

# Convertir datos de entrenamiento y prueba a BIOES
train_esp_bioes = [convert_bio_to_bioes(sent) for sent in train_esp]
dev_esp_bioes = [convert_bio_to_bioes(sent) for sent in dev_esp]
test_esp_bioes = [convert_bio_to_bioes(sent) for sent in test_esp]

# Crear una instancia de CRFTagger
crf_tagger_esp = CRFTagger()

# Entrenar el modelo CRF con los datos de entrenamiento en español convertidos a BIOES
crf_tagger_esp.train(train_esp_bioes, 'model_crf_esp_bioes.crf.tagger')

# Etiquetar los conjuntos de desarrollo y prueba
etiquetadas_dev_esp_bioes = crf_tagger_esp.tag_sents([[word for word, _ in sent] for sent in dev_esp_bioes])
etiquetadas_test_esp_bioes = crf_tagger_esp.tag_sents([[word for word, _ in sent] for sent in test_esp_bioes])

# Comparar las etiquetas predichas con las reales para calcular la precisión
def calcular_precision(predichas, reales):
    correctos = sum(1 for pred_sent, real_sent in zip(predichas, reales) for pred, real in zip(pred_sent, real_sent) if pred[1] == real[1])
    total = sum(len(sent) for sent in reales)
    return correctos / total

precision_dev = calcular_precision(etiquetadas_dev_esp_bioes, dev_esp_bioes)
precision_test = calcular_precision(etiquetadas_test_esp_bioes, test_esp_bioes)

print("Precisión en conjunto de desarrollo:", precision_dev)
print("Precisión en conjunto de prueba:", precision_test)


ValueError: not enough values to unpack (expected 2, got 0)